In [1]:
%load_ext autoreload
%autoreload 2

# MLflow Regression Pipeline Notebook

This notebook runs the MLflow Regression Pipeline on Databricks and inspects its results. For more information about the MLflow Regression Pipeline, including usage examples, see the [Regression Pipeline overview documentation](https://mlflow.org/docs/latest/pipelines.html#regression-pipeline) the [Regression Pipeline API documentation](https://mlflow.org/docs/latest/python_api/mlflow.pipelines.html#module-mlflow.pipelines.regression.v1.pipeline).

In [2]:
from mlflow.pipelines import Pipeline

p = Pipeline(profile="local")

2022/07/29 20:22:19 INFO mlflow.pipelines.pipeline: Creating MLflow Pipeline 'mlp-regression-template' with profile: 'local'


In [3]:
p.clean()

In [4]:
p.inspect()

In [5]:
p.run("ingest")

2022/07/29 20:22:49 INFO mlflow.pipelines.steps.ingest.datasets: Resolving input data from '['/home/nys/Desktop/stock_pjt/mlflow-exercise/mlp-regression-template/data/sample.parquet']'
2022/07/29 20:22:49 INFO mlflow.pipelines.steps.ingest.datasets: Resolved input data to '/tmp/tmpazm3qr20/sample.parquet'
2022/07/29 20:22:49 INFO mlflow.pipelines.steps.ingest.datasets: Converting dataset to parquet format, if necessary
2022/07/29 20:22:49 INFO mlflow.pipelines.steps.ingest: Successfully stored data in parquet format at '/home/nys/.mlflow/pipelines/bbc087fef70f864a40702b4e3c3beab7e14e88af2aeb2fc5d41c7a38f21d0369/steps/ingest/outputs/dataset.parquet'
2022/07/29 20:22:49 INFO mlflow.pipelines.steps.ingest: Profiling ingested dataset
2022/07/29 20:22:51 INFO mlflow.pipelines.steps.ingest: Wrote dataset profile to '/home/nys/.mlflow/pipelines/bbc087fef70f864a40702b4e3c3beab7e14e88af2aeb2fc5d41c7a38f21d0369/steps/ingest/outputs/dataset_profile.html'


In [6]:
p.run("split")

2022/07/29 20:23:08 INFO mlflow.pipelines.steps.split: Creating hash buckets on input dataset containing 10000 rows consumes 0.04539966583251953 seconds.
2022/07/29 20:23:08 INFO mlflow.pipelines.steps.split: Split dataset result: train split (8051 rows), validation split (959 rows), test split (990 rows).


In [8]:
p.run("transform")

In [9]:
p.run("train")

2022/07/29 20:23:43 INFO mlflow.store.db.utils: Creating initial MLflow database tables...
2022/07/29 20:23:43 INFO mlflow.store.db.utils: Updating database tables
INFO  [alembic.runtime.migration] Context impl SQLiteImpl.
INFO  [alembic.runtime.migration] Will assume non-transactional DDL.
INFO  [alembic.runtime.migration] Running upgrade  -> 451aebb31d03, add metric step
INFO  [alembic.runtime.migration] Running upgrade 451aebb31d03 -> 90e64c465722, migrate user column to tags
INFO  [alembic.runtime.migration] Running upgrade 90e64c465722 -> 181f10493468, allow nulls for metric values
INFO  [alembic.runtime.migration] Running upgrade 181f10493468 -> df50e92ffc5e, Add Experiment Tags Table
INFO  [alembic.runtime.migration] Running upgrade df50e92ffc5e -> 7ac759974ad8, Update run tags with larger limit
INFO  [alembic.runtime.migration] Running upgrade 7ac759974ad8 -> 89d4b8295536, create latest metrics table
INFO  [89d4b8295536_create_latest_metrics_table_py] Migration complete!
INFO  

In [10]:
p.run("evaluate")

2022/07/29 20:23:56 INFO mlflow.models.evaluation.base: Evaluating the model with the default evaluator.
/home/nys/anaconda3/envs/mlflow-exercise/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but SGDRegressor was fitted with feature names
  warnings.warn(
/home/nys/anaconda3/envs/mlflow-exercise/lib/python3.8/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but SGDRegressor was fitted with feature names
  warnings.warn(
X does not have valid feature names, but SGDRegressor was fitted with feature names
2022/07/29 20:23:56 INFO mlflow.models.evaluation.default_evaluator: Shap explainer _PatchedKernelExplainer is used.

  0%|          | 0/10 [00:00<?, ?it/s]X does not have valid feature names, but SGDRegressor was fitted with feature names
X does not have valid feature names, but SGDRegressor was fitted with feature names
X does not have valid feature names, but SGDRegressor was fitted with feature n

In [11]:
p.run("register")

Successfully registered model 'taxi_fare_regressor'.
2022/07/29 20:24:04 INFO mlflow.tracking._model_registry.client: Waiting up to 300 seconds for model version to finish creation.                     Model name: taxi_fare_regressor, version 1
Created version '1' of model 'taxi_fare_regressor'.


In [12]:
p.inspect("train")

In [13]:
test_data = p.get_artifact("test_data")
test_data.describe()

trip_distance  fare_amount    pickup_zip   dropoff_zip  pickup_dow  \
count     987.000000   987.000000    987.000000    987.000000  987.000000   
mean        2.844630    12.180355  10130.107396  10171.005066    3.180344   
std         3.479708     9.832273    317.412339    376.237618    1.976510   
min         0.030000     0.010000  10001.000000   7423.000000    0.000000   
25%         1.000000     6.500000  10012.000000  10013.000000    1.000000   
50%         1.680000     9.000000  10022.000000  10023.000000    3.000000   
75%         2.995000    14.000000  10110.000000  10119.000000    5.000000   
max        24.490000    75.500000  11436.000000  11435.000000    6.000000   

       pickup_hour  trip_duration  
count   987.000000     987.000000  
mean     13.680851      13.646707  
std       6.353072      19.105446  
min       0.000000       0.200000  
25%       9.000000       6.441667  
50%      14.000000      10.283333  
75%      19.000000      16.775000  
max      23.000000     517.000000

In [14]:
trained_model = p.get_artifact("model")
print(trained_model)

mlflow.pyfunc.loaded_model:
  artifact_path: train/model
  flavor: mlflow.sklearn
  run_id: f4d7d3718f35461e82f359fc1f63b7db

